In [2]:
import pickle
from keras_preprocessing.text import tokenizer_from_json

In [3]:
#loading tokenizer
with open('D:/Job_prediction/tokenizer.pickle', 'rb') as handle:
    tokenizer = pickle.load(handle)


In [4]:
# loading our model
from keras.models import load_model
model = load_model('D:/Job_prediction/skill_prediction.h5')

In [2]:
from keras_preprocessing.sequence import pad_sequences
def predict(model,tokenizer,word):
    input = pad_sequences(tokenizer.texts_to_sequences([word]),maxlen=20)
    # input = tokenizer.texts_to_sequences([word])
    d = model.predict(input)
    # print('probebilty ',d)
    if d <= 0.5:
        d = 0 #'non skill word'
    else:
        d = 1 #'skill word' 
    return d

In [5]:
import pandas as pd
import numpy as np
DA = pd.read_csv('D:/Job_prediction/dataAnalyst.csv')
DA

Title      Company name      2  \
0                                    Data Analyst  8Twelve Mortgage  404.0   
1                           Data Analyst (Hybrid)           Moneris    3.4   
2                             Data Analyst (#124)              Cota    3.8   
3                     Analyst, Data and Analytics    Ontario Health    4.1   
4                                Jr. Data Analyst      Flex Surveys    5.0   
..                                            ...               ...    ...   
445                Analyst, Investment Management   Northland Power    3.8   
446   SAP Business System Analyst (1 yr contract)         Purolator    3.5   
447                        Senior Workday Analyst             Braze  404.0   
448  Senior Business Systems Analyst - Salesforce             TELUS    3.9   
449                      Customer Service Analyst           FERRERO    4.0   

                          address                         date  \
0                     Toronto, ON    Posted\nPosted 8 days ago   
1    Hybrid remote in Toronto, ON    Posted\nPosted 3 days ago   
2                     Toronto, ON   Posted\nPosted 11 days ago   
3                     Toronto, ON  Posted\nPosted 30+ days ago   
4        Greater Toronto Area, ON    Posted\nPosted 4 days ago   
..                            ...                          ...   
445                   Toronto, ON  Posted\nPosted 30+ days ago   
446               Mississauga, ON  Posted\nPosted 30+ days ago   
447         Remote in Toronto, ON   Posted\nPosted 15 days ago   
448                   Toronto, ON   Posted\nPosted 26 days ago   
449                   Toronto, ON  Posted\nPosted 30+ days ago   

                                           Description  
0    Job Summary:\nThe Data Analyst will be respons...  
1    Who we are\nMoneris was created as a joint inv...  
2    EXTERNAL JOB POSTING #124\nPosted: 04 October ...  
3    Ontario Health actively seeks candidates who a...  
4    We are looking for someone that can follow ins...  
..                                                 ...  
445  Who We Are:\n\nAt Northland, we’re enablers of...  
446  Workplace Environment: Hybrid\n\nThis role can...  
447  Braze (Nasdaq: BRZE) is a leading, comprehensi...  
448  Location: Toronto, ON, CA Calgary, AB, CA Winn...  
449  Job Location:\nToronto, Ontario\nCompany descr...  

[450 rows x 6 columns]

In [6]:
desc = DA.Description

In [44]:
desc

(450,)

In [14]:
desc = desc.reshape(-1,1)

In [17]:
desc.shape

(450, 1)

In [7]:
import spacy
#Initializing the spacy engine and then use it to process the text:
nlp = spacy.load('en_core_web_sm')



In [8]:
from pandas.core.arrays.sparse import dtype


df_nouns = np.empty(shape=(len(desc)),dtype=str)

In [9]:
# df_nouns[0] = 1
df_nouns.shape

(450,)

In [17]:
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.tokenize.treebank import TreebankWordDetokenizer
 
# remove stopwords function
def remove_stopwords(text):
    stop_words = set(stopwords.words("english"))
    word_tokens = word_tokenize(text)
    filtered_text = [word for word in word_tokens if word not in stop_words]
    r = TreebankWordDetokenizer().detokenize(filtered_text)
    return r
    
# example_text = ["This is a sample", "sentence and we are", "going to remove" ,"the stopwords from this."]
# for i in example_text:
#     remove_stopwords(i)

In [45]:
def remove_punctuation(text):
    translator = str.maketrans('', '', string.punctuation)
    print(text.translate(translator))
d = ["This is a. sample", "sentence's and we are", "going, to remove" ,"the stopwords from this."]
for i in d:
    remove_punctuation(i)

This is a sample
sentences and we are
going to remove
the stopwords from this


In [49]:
import nltk
import string
import re

# remove punctuation
def remove_punctuation(text):
    translator = str.maketrans('', '', string.punctuation)
    return text.translate(translator)

def text_preprocess(text):
    r = text.lower() # coverting into lower case
    r = remove_stopwords(r) # removing stop words
    r = re.sub(r'\d+', '', r) # removing numbers
    r = remove_punctuation(r) # removing punctuations
    r = " ".join(r.split()) # removing white sapce
    r = ''.join(r.splitlines()) # removing newline character
    return r
    




In [48]:
d[0].split()

['This', 'is', 'a.', 'sample']

In [51]:
for i in d:
    r = i.lower() # coverting into lower case
    r = remove_stopwords(r) # removing stop words
    r = re.sub(r'\d+', '', r) # removing numbers
    r = remove_punctuation(r) # removing punctuations
    r = " ".join(r.split()) # removing white sapce
    r = ''.join(r.splitlines()) # removing newline character
    print(r)

a sample
sentence s
going remove
stopwords


In [82]:

df_nouns = np.empty(shape=(len(desc)),dtype=object)
for i in range(len(desc)):
    nouns = []
    doc = nlp(str(desc[i]).lower())
    for chunk in doc.noun_chunks:
        chunk = text_preprocess(str(chunk))
        nouns.append(chunk)
    df_nouns[i] = nouns


In [83]:
df_nouns.shape

(450,)

In [81]:
type(df_nouns)

numpy.ndarray

In [86]:
df_nouns[0][0]

'job summary'

In [64]:
df_nouns

array([[list(['job summary', 'data analyst', 'data', 'needs', 'brokerage', 'role', 'internal stakeholders', 'business problem formulation', 'relevant data sources', 'sub', '', 'processes', '', 'new kpis', 'new data extract requirements', 'data', 'multiple sources', 'highquality insights', '', 'full narrative', 'role', 'significant amount', 'collaboration', 'successful person', 'multiple critical projects', '', 'diverse inclusive authentic workplace', 'position overview', 'advanced skills', 'data analysis', 'profiling', 'data mapping', 'data modeling', 'data lakes', 'analytics data analytics', 'aws quicksight redshift data migration', 'sql', 'etl scripting', 'integration', 'rest apis', 'nodejs aws lambdaapi gateway detailed duties', 'scriptingprogramming skills', 'various types', 'source data', 'wellprepared datasets', 'multiple levels', 'granularities', 'eg demographics', 'customers', 'products', 'transactions', 'development', 'standard customized reporting', 'dashboards', 'analysis', 

In [56]:
df_copy =  df_nouns.copy()

In [114]:
from keras_preprocessing.sequence import pad_sequences
def predict(model,tokenizer,word):
    input = pad_sequences(tokenizer.texts_to_sequences([word]),maxlen=20)
    # input = tokenizer.texts_to_sequences([word])
    d = model.predict(input)
    # print(d)
    # print('probebilty ',d)
    if d <= 0.5:
        d = 0 #'non skill word'
    else:
        d = 1 #'skill word' 
    # print(d)
    return d

In [115]:
len(df_nouns)

450

In [116]:
dir_noun = dict()
# dir_noun[df_nouns[0][0]] = 1
for i in range(len(df_nouns)):
    dir_temp = dict()
    for j in df_nouns[i]:
        # print(type(i))
        r = predict(model,tokenizer,j)
        dir_temp[j] = r
    dir_noun[i] = dir_temp


1/1 [==============================] - 0s 158ms/step


KeyboardInterrupt: 

In [119]:
len(dir_noun)

265

In [123]:
import json
with open("dir_json.json", "w") as outfile:
    json.dump(dir_noun, outfile)

In [113]:
dir_noun

{'job summary': 0,
 'data analyst': 1,
 'data': 1,
 'needs': 0,
 'brokerage': 0,
 'role': 0,
 'internal stakeholders': 0,
 'business problem formulation': 0,
 'relevant data sources': 0,
 'sub': 0,
 '': 0,
 'processes': 0,
 'new kpis': 0,
 'new data extract requirements': 1,
 'multiple sources': 0,
 'highquality insights': 0,
 'full narrative': 0,
 'significant amount': 0,
 'collaboration': 0,
 'successful person': 0,
 'multiple critical projects': 0,
 'diverse inclusive authentic workplace': 0,
 'position overview': 0,
 'advanced skills': 1,
 'data analysis': 1,
 'profiling': 0,
 'data mapping': 1,
 'data modeling': 1,
 'data lakes': 1,
 'analytics data analytics': 1,
 'aws quicksight redshift data migration': 1,
 'sql': 1,
 'etl scripting': 1,
 'integration': 1,
 'rest apis': 1,
 'nodejs aws lambdaapi gateway detailed duties': 1,
 'scriptingprogramming skills': 0,
 'various types': 0,
 'source data': 1,
 'wellprepared datasets': 1,
 'multiple levels': 0,
 'granularities': 0,
 'eg dem

In [80]:
type(df_nouns[0])

numpy.ndarray

In [72]:
dir_noun

{1: [['job summary',
   'data analyst',
   'data',
   'needs',
   'brokerage',
   'role',
   'internal stakeholders',
   'business problem formulation',
   'relevant data sources',
   'sub',
   '',
   'processes',
   '',
   'new kpis',
   'new data extract requirements',
   'data',
   'multiple sources',
   'highquality insights',
   '',
   'full narrative',
   'role',
   'significant amount',
   'collaboration',
   'successful person',
   'multiple critical projects',
   '',
   'diverse inclusive authentic workplace',
   'position overview',
   'advanced skills',
   'data analysis',
   'profiling',
   'data mapping',
   'data modeling',
   'data lakes',
   'analytics data analytics',
   'aws quicksight redshift data migration',
   'sql',
   'etl scripting',
   'integration',
   'rest apis',
   'nodejs aws lambdaapi gateway detailed duties',
   'scriptingprogramming skills',
   'various types',
   'source data',
   'wellprepared datasets',
   'multiple levels',
   'granularities',
   '

In [ ]:
dir_noun = {}
for i in df_nouns:
    

In [102]:
df_nouns[0][0]

'job summary'

In [105]:
df_copy[0][0]

['job summary',
 'data analyst',
 'data',
 'needs',
 'brokerage',
 'role',
 'internal stakeholders',
 'business problem formulation',
 'relevant data sources',
 'sub',
 '',
 'processes',
 '',
 'new kpis',
 'new data extract requirements',
 'data',
 'multiple sources',
 'highquality insights',
 '',
 'full narrative',
 'role',
 'significant amount',
 'collaboration',
 'successful person',
 'multiple critical projects',
 '',
 'diverse inclusive authentic workplace',
 'position overview',
 'advanced skills',
 'data analysis',
 'profiling',
 'data mapping',
 'data modeling',
 'data lakes',
 'analytics data analytics',
 'aws quicksight redshift data migration',
 'sql',
 'etl scripting',
 'integration',
 'rest apis',
 'nodejs aws lambdaapi gateway detailed duties',
 'scriptingprogramming skills',
 'various types',
 'source data',
 'wellprepared datasets',
 'multiple levels',
 'granularities',
 'eg demographics',
 'customers',
 'products',
 'transactions',
 'development',
 'standard customized

In [111]:
for i in df_nouns[0]:
    predict(model,tokenizer,i)

1/1 [==============================] - 0s 42ms/step
0
1/1 [==============================] - 0s 42ms/step
1
1/1 [==============================] - 0s 49ms/step
1
1/1 [==============================] - 0s 53ms/step
0
1/1 [==============================] - 0s 51ms/step
0
1/1 [==============================] - 0s 58ms/step
0
1/1 [==============================] - 0s 63ms/step
0
1/1 [==============================] - 0s 62ms/step
0
1/1 [==============================] - 0s 51ms/step
0
1/1 [==============================] - 0s 51ms/step
0
1/1 [==============================] - 0s 49ms/step
0
1/1 [==============================] - 0s 49ms/step
0
1/1 [==============================] - 0s 40ms/step
0
1/1 [==============================] - 0s 47ms/step
0
1/1 [==============================] - 0s 41ms/step
1
1/1 [==============================] - 0s 41ms/step
1
1/1 [==============================] - 0s 37ms/step
0
1/1 [==============================] - 0s 48ms/step
0
1/1 [=======================

KeyboardInterrupt: 